Importing cellular automata & optimization classes, and other stuff

In [1]:
import os
import sys
import shutil

from typing import List, Type, Callable, Dict
from numpy import int32
from numpy._typing import NDArray
import importlib

sys.path.append(os.path.dirname(os.path.dirname(os.path.abspath(''))))

#from algorithm.blender import Lattice, clear_initial
from algorithm.genetic import Optimizer, Mutator, ArbitraryRulesetMutator
from algorithm.objectives import sampleobj, surface_to_vol, surfacecalc

import numpy as np
import pandas as pd

import time

Setting up optimizer and data logging code

In [2]:
def log_mutation(data_list: List[Dict], mutations: List[tuple[List,List]], objective_val: float):
    """
    Given the data list reference, the mutation set, and the objective value after applying it, add it to the data logging list
    """
    ic_cell_pos = []
    ic_state_old = []
    ic_state_new = []
    srt_cell_pos = []
    srt_state_old = []
    srt_state_new = []

    """
    Important difference from original genetic algorithm: 
    ic_mut is a 4 membered list showing the mutated position in the IC.
    Example: [0,0,0,1], meaning that at IC pos (0,0) the state 0 is modified to be 1.
    srt_mut is a 6 membered list showing the mutated position in the ruleset.
    Example: [0,0,0,0,0,1], meaning that at SRT rule pos (0,0,0) index 0 the rule 0 is modified to be 1.
    For a 2 state SRT there are 18 different cells for mutation: 0 - 17.
    """
    for ic_mut in mutations[0]:
        ic_cell_pos.append(tuple(ic_mut[0:2]))
        ic_state_old.append(ic_mut[2])
        ic_state_new.append(ic_mut[3])
    for srt_mut in mutations[1]:
        srt_cell_pos.append(tuple(srt_mut[0:4]))
        srt_state_old.append(srt_mut[4])
        srt_state_new.append(srt_mut[5])
    # print(f"Number of IC mutations: {len(mutations[0])}, Number of SRT mutations: {len(mutations[1])}", end='\r')
    data_list.append({
        "ic_cell_pos": np.array(ic_cell_pos), 
        "ic_state_old": np.array(ic_state_old), 
        "ic_state_new": np.array(ic_state_new), 
        "srt_cell_pos": np.array(srt_cell_pos), 
        "srt_state_old": np.array(srt_state_old), 
        "srt_state_new": np.array(srt_state_new), 
        "objective": objective_val,
    })

itlogs = [0]

def run_experiment(iters: int, grid_sz: int, opt_func: Callable[[NDArray[int32]], int], ic_num_mutate: int, srt_num_mutate: int, rule_mutate_prob: float, strict: bool = False, num_strict: bool = True, states: int = 2, ic_enable: bool = True, srt_enable: bool = True):
    """
    Runs an experiment with the below hyperparameters:

    :param iters: The number of iterations the mutation algorithm (updating both IC and SRT) is going to run for
    :param grid_sz: The size of the square grid that we're going to update each iteration
    :param opt_func: The functions that gives the performance metric we're going to optimize
    :param srt_num_mutate: The number of SRT cells for which we're going to mutate the rule applied, each iteration
    :param ic_num_mutate: The number of IC cells for which we're going to mutate the rule applied, each iteration
    :param rule_mutate_prob: The probability, for each neighbor state tensor of the rule of a cell that's selected to be mutated, the final state is mutated
    :param strict: Whether SRT mutations are chosen by cell then rule or by rule directly; for more info, see mutations.py
    :param num_strict: Whether the number of SRT/IC cells mutated will be constant per iteration or variable; for more info, see mutations.py
    :param states: The number of states the NSICA will run on; for more info, see nsica.py
    :param ic_enable: Whether the IC will be mutated
    :param srt_enable: Whether the SRT will be mutated

    Params ruleset_mutator_class and rule_set have been deleted due to previous deletion of the RulesetMutator class.
    """

    # RESOLVED: separate SRT and IC mutations to have a certain number of each
    # RESOLVED: add a flag to enable doing only SRT or only IC mutations in an iteration (in optimizer step, and then propagate into mutator)

    ruleset_mutator = ArbitraryRulesetMutator(grid_size=grid_sz, mutate_p=1/(grid_sz**2) * (srt_num_mutate+ic_num_mutate), rule_mutate_p=rule_mutate_prob, strict=strict, num_strict = num_strict, ic_ct = ic_num_mutate, srt_ct = srt_num_mutate, states=states, ic_enable=ic_enable, srt_enable = srt_enable)

    optim = Optimizer(mutator=ruleset_mutator, objective=lambda grid: opt_func(grid))
    """
    Pandas Dataframe used to log experiment data is:

    ic_cell_pos (np.array) | ic_state_old (np.array) | ic_state_new (np.array) | srt_cell_pos (np.array) | srt_state_old (np.array) | srt_state_new (np.array) | objective (float)
    
    etc.

    initial state for IC is in entry 0 in ic_state_old, and SRT is in entry 0 in srt_state_old

    ic and srt mutation cell positions and states can have an extra dimension in the beginning to indicate they are batch updates
    """

    init_state = optim.state
    
    data_list = [{"ic_cell_pos": grid_sz, 
                  "ic_state_old": init_state[0], 
                  "ic_state_new": None, 
                  "srt_cell_pos": -1, 
                  "srt_state_old": init_state[1], 
                  "srt_state_new": None, 
                  "objective": 0}]

    for it in range(iters):
        # print(f"Iteration {it}", end='\r')
        # print(f"On iteration {it+1}...")
        accepted, new, old, mutations = optim.step()
        # data logging
        log_mutation(data_list, mutations, optim.objvalue)
        itlogs.append(float(optim.objvalue))
        if accepted:
           print(f"Got a better state: {optim.objvalue} at iteration {it}, which is {(100*optim.objvalue/(-98304)):.3f}% of the ground truth.")

    # print(data_list)
    df = pd.DataFrame(data_list)
    # print(df)
    return df

timelogs = []

def repeat_experiment(experiment_name: str, num_expers: int, *args):
    """
    Perform (sequentially) multiple experiments that return a Pandas DataFrame and save all the data

    :param experiment_name: The name of the experiment to save the file
    :param num_expers: Number of times to run the experiment (and save all the data in one file)
    :param *args: The arguments to be passed to the experiment function

    Within *args should be a states parameter, denoting the number of NSICA states.
    """
    for i in range(num_expers):
        init = time.time()
        print(f'REPETITION {i}')
        ret_data = run_experiment(*args)
        timelogs.append(time.time() - init)
        print(f"Finished rep {i} in {time.time() - init}s")
        ret_data.to_hdf(f'test/{states}/{experiment_name}_{i}_{states}states.h5', key='data', mode='a')


Setting up experiments and gathering data

In [3]:
ITERATIONS_SET = [10000]
GRID_SIZE_SET = [32]
NUM_REPEAT = 1
EXPERIMENT_NAME = "statetimetest"
STATE_SET = [2]
NUMS_SET = [(1, 18), (2, 36), (5, 90), (10, 180), (20, 360), (50, 900), (100, 1800), (200, 3600), (500, 9000), (1000, 18000), (2000, 36000)]
for iters in ITERATIONS_SET:
    for grid_sz in GRID_SIZE_SET:
        for states in STATE_SET:
            for nums in NUMS_SET:
                print(f"RUNNING EXPERIMENT {EXPERIMENT_NAME} WITH {iters} ITERATIONS AND {grid_sz} SIZE GRID AND {states} STATES, CT_TUPLE = {nums}")
                #Default probability for Strict Mode = 2/3; default probability for Non-Strict Mode = 5/384
                #Default number of IC mutations = 20, default number of SRT mutations = 240
                repeat_experiment(f"{EXPERIMENT_NAME}_{iters}ITERS_{grid_sz}GRID", NUM_REPEAT, iters, grid_sz, surfacecalc, nums[0], nums[1], 5/384, False, True, states, True, True)
                print(itlogs)

RUNNING EXPERIMENT statetimetest WITH 10000 ITERATIONS AND 32 SIZE GRID AND 2 STATES, CT_TUPLE = (1, 18)
REPETITION 0
Got a better state: -2074 at iteration 0, which is 2.110% of the ground truth.
Got a better state: -2082 at iteration 1, which is 2.118% of the ground truth.
Got a better state: -2098 at iteration 2, which is 2.134% of the ground truth.
Got a better state: -2102 at iteration 3, which is 2.138% of the ground truth.
Got a better state: -2110 at iteration 4, which is 2.146% of the ground truth.
Got a better state: -2118 at iteration 5, which is 2.155% of the ground truth.
Got a better state: -2126 at iteration 6, which is 2.163% of the ground truth.
Got a better state: -2134 at iteration 7, which is 2.171% of the ground truth.
Got a better state: -2138 at iteration 8, which is 2.175% of the ground truth.
Got a better state: -2142 at iteration 9, which is 2.179% of the ground truth.
Got a better state: -2144 at iteration 10, which is 2.181% of the ground truth.
Got a better

C:\Users\LAMM\AppData\Local\Temp\ipykernel_9544\3651072940.py:121: PerformanceWarning: 
your performance may suffer as PyTables will pickle object types that it cannot
map directly to c-types [inferred_type->mixed-integer,key->block0_values] [items->Index(['ic_cell_pos', 'ic_state_old', 'ic_state_new', 'srt_cell_pos',
       'srt_state_old', 'srt_state_new', 'objective'],
      dtype='object')]

  ret_data.to_hdf(f'test/{states}/{experiment_name}_{i}_{states}states.h5', key='data', mode='a')


[0, -2074.0, -2082.0, -2098.0, -2102.0, -2110.0, -2118.0, -2126.0, -2134.0, -2138.0, -2142.0, -2144.0, -2154.0, -2160.0, -2166.0, -2166.0, -2174.0, -2182.0, -2190.0, -2204.0, -2208.0, -2218.0, -2224.0, -2234.0, -2236.0, -2258.0, -2262.0, -2282.0, -2288.0, -2292.0, -2298.0, -2306.0, -2322.0, -2330.0, -2332.0, -2348.0, -2352.0, -2354.0, -2362.0, -2364.0, -2370.0, -2372.0, -2382.0, -2386.0, -2388.0, -2388.0, -2388.0, -2408.0, -2416.0, -2416.0, -2416.0, -2424.0, -2426.0, -2432.0, -2432.0, -2432.0, -2454.0, -2468.0, -2480.0, -2488.0, -2504.0, -2516.0, -2516.0, -2524.0, -2524.0, -2530.0, -2538.0, -2546.0, -2554.0, -2556.0, -2568.0, -2568.0, -2572.0, -2572.0, -2574.0, -2574.0, -2576.0, -2578.0, -2600.0, -2610.0, -2620.0, -2624.0, -2626.0, -2632.0, -2632.0, -2644.0, -2650.0, -2658.0, -2662.0, -2674.0, -2684.0, -2696.0, -2704.0, -2716.0, -2724.0, -2728.0, -2734.0, -2746.0, -2758.0, -2764.0, -2766.0, -2772.0, -2786.0, -2790.0, -2800.0, -2804.0, -2804.0, -2808.0, -2808.0, -2812.0, -2812.0, -2828.

C:\Users\LAMM\AppData\Local\Temp\ipykernel_9544\3651072940.py:121: PerformanceWarning: 
your performance may suffer as PyTables will pickle object types that it cannot
map directly to c-types [inferred_type->mixed-integer,key->block0_values] [items->Index(['ic_cell_pos', 'ic_state_old', 'ic_state_new', 'srt_cell_pos',
       'srt_state_old', 'srt_state_new', 'objective'],
      dtype='object')]

  ret_data.to_hdf(f'test/{states}/{experiment_name}_{i}_{states}states.h5', key='data', mode='a')


[0, -2074.0, -2082.0, -2098.0, -2102.0, -2110.0, -2118.0, -2126.0, -2134.0, -2138.0, -2142.0, -2144.0, -2154.0, -2160.0, -2166.0, -2166.0, -2174.0, -2182.0, -2190.0, -2204.0, -2208.0, -2218.0, -2224.0, -2234.0, -2236.0, -2258.0, -2262.0, -2282.0, -2288.0, -2292.0, -2298.0, -2306.0, -2322.0, -2330.0, -2332.0, -2348.0, -2352.0, -2354.0, -2362.0, -2364.0, -2370.0, -2372.0, -2382.0, -2386.0, -2388.0, -2388.0, -2388.0, -2408.0, -2416.0, -2416.0, -2416.0, -2424.0, -2426.0, -2432.0, -2432.0, -2432.0, -2454.0, -2468.0, -2480.0, -2488.0, -2504.0, -2516.0, -2516.0, -2524.0, -2524.0, -2530.0, -2538.0, -2546.0, -2554.0, -2556.0, -2568.0, -2568.0, -2572.0, -2572.0, -2574.0, -2574.0, -2576.0, -2578.0, -2600.0, -2610.0, -2620.0, -2624.0, -2626.0, -2632.0, -2632.0, -2644.0, -2650.0, -2658.0, -2662.0, -2674.0, -2684.0, -2696.0, -2704.0, -2716.0, -2724.0, -2728.0, -2734.0, -2746.0, -2758.0, -2764.0, -2766.0, -2772.0, -2786.0, -2790.0, -2800.0, -2804.0, -2804.0, -2808.0, -2808.0, -2812.0, -2812.0, -2828.

...

[0, -2074.0, -2082.0, -2098.0, -2102.0, -2110.0, -2118.0, -2126.0, -2134.0, -2138.0, -2142.0, -2144.0, -2154.0, -2160.0, -2166.0, -2166.0, -2174.0, -2182.0, -2190.0, -2204.0, -2208.0, -2218.0, -2224.0, -2234.0, -2236.0, -2258.0, -2262.0, -2282.0, -2288.0, -2292.0, -2298.0, -2306.0, -2322.0, -2330.0, -2332.0, -2348.0, -2352.0, -2354.0, -2362.0, -2364.0, -2370.0, -2372.0, -2382.0, -2386.0, -2388.0, -2388.0, -2388.0, -2408.0, -2416.0, -2416.0, -2416.0, -2424.0, -2426.0, -2432.0, -2432.0, -2432.0, -2454.0, -2468.0, -2480.0, -2488.0, -2504.0, -2516.0, -2516.0, -2524.0, -2524.0, -2530.0, -2538.0, -2546.0, -2554.0, -2556.0, -2568.0, -2568.0, -2572.0, -2572.0, -2574.0, -2574.0, -2576.0, -2578.0, -2600.0, -2610.0, -2620.0, -2624.0, -2626.0, -2632.0, -2632.0, -2644.0, -2650.0, -2658.0, -2662.0, -2674.0, -2684.0, -2696.0, -2704.0, -2716.0, -2724.0, -2728.0, -2734.0, -2746.0, -2758.0, -2764.0, -2766.0, -2772.0, -2786.0, -2790.0, -2800.0, -2804.0, -2804.0, -2808.0, -2808.0, -2812.0, -2812.0, -2828.

C:\Users\LAMM\AppData\Local\Temp\ipykernel_9544\3651072940.py:121: PerformanceWarning: 
your performance may suffer as PyTables will pickle object types that it cannot
map directly to c-types [inferred_type->mixed-integer,key->block0_values] [items->Index(['ic_cell_pos', 'ic_state_old', 'ic_state_new', 'srt_cell_pos',
       'srt_state_old', 'srt_state_new', 'objective'],
      dtype='object')]

  ret_data.to_hdf(f'test/{states}/{experiment_name}_{i}_{states}states.h5', key='data', mode='a')


[0, -2074.0, -2082.0, -2098.0, -2102.0, -2110.0, -2118.0, -2126.0, -2134.0, -2138.0, -2142.0, -2144.0, -2154.0, -2160.0, -2166.0, -2166.0, -2174.0, -2182.0, -2190.0, -2204.0, -2208.0, -2218.0, -2224.0, -2234.0, -2236.0, -2258.0, -2262.0, -2282.0, -2288.0, -2292.0, -2298.0, -2306.0, -2322.0, -2330.0, -2332.0, -2348.0, -2352.0, -2354.0, -2362.0, -2364.0, -2370.0, -2372.0, -2382.0, -2386.0, -2388.0, -2388.0, -2388.0, -2408.0, -2416.0, -2416.0, -2416.0, -2424.0, -2426.0, -2432.0, -2432.0, -2432.0, -2454.0, -2468.0, -2480.0, -2488.0, -2504.0, -2516.0, -2516.0, -2524.0, -2524.0, -2530.0, -2538.0, -2546.0, -2554.0, -2556.0, -2568.0, -2568.0, -2572.0, -2572.0, -2574.0, -2574.0, -2576.0, -2578.0, -2600.0, -2610.0, -2620.0, -2624.0, -2626.0, -2632.0, -2632.0, -2644.0, -2650.0, -2658.0, -2662.0, -2674.0, -2684.0, -2696.0, -2704.0, -2716.0, -2724.0, -2728.0, -2734.0, -2746.0, -2758.0, -2764.0, -2766.0, -2772.0, -2786.0, -2790.0, -2800.0, -2804.0, -2804.0, -2808.0, -2808.0, -2812.0, -2812.0, -2828.

C:\Users\LAMM\AppData\Local\Temp\ipykernel_9544\3651072940.py:121: PerformanceWarning: 
your performance may suffer as PyTables will pickle object types that it cannot
map directly to c-types [inferred_type->mixed-integer,key->block0_values] [items->Index(['ic_cell_pos', 'ic_state_old', 'ic_state_new', 'srt_cell_pos',
       'srt_state_old', 'srt_state_new', 'objective'],
      dtype='object')]

  ret_data.to_hdf(f'test/{states}/{experiment_name}_{i}_{states}states.h5', key='data', mode='a')


OverflowError: Python int too large to convert to C long

In [ ]:
print(timelogs)

In [ ]:
print(itlogs)
